In [1]:
import numpy as np
import scanpy as sc
from scipy.sparse import csr_matrix
import logging
import pandas as pd
import patsy
import matplotlib.pyplot as plt
%matplotlib inline 

In [2]:
sc.settings.verbosity = 3             # verbosity: errors (0), warnings (1), info (2), hints (3)
sc.logging.print_versions()
sc.settings.set_figure_params(dpi=80)
sc.settings.autoshow = True
logging.basicConfig(level=logging.INFO)
logging.getLogger().setLevel(logging.INFO)

scanpy==1.5.0 anndata==0.7.3 umap==0.4.3 numpy==1.18.4 scipy==1.4.1 pandas==1.0.3 scikit-learn==0.23.1 statsmodels==0.11.1 python-igraph==0.8.2 leidenalg==0.8.1


/home/ssm-user/anaconda3/envs/r_env/lib/python3.7/site-packages/umap/spectral.py:4: NumbaDeprecationWarning: No direct replacement for 'numba.targets' available. Visit https://gitter.im/numba/numba-dev to request help. Thanks!
  import numba.targets


## **Add donor name and timepoint to batch corrected object**

### Make a subset of adata_combat per run

In [47]:
# Combined mRNA and protein, high_res cell type classification based on mRNA first --> subclustering mRNA and protein --> T_subset further specified based on protein
#adata_combat.obs['cell_type_highres'] and ['cell_type_major_highres'] are the most precise cell type classification
adata_combat = sc.read('/data/count_matrices/covid19/combined/run12345_combi_final2.h5ad')

In [34]:
# Read csv file with freemux_cluster assignment match between runs (output George Notebook check.matchup.sc.output.ipynb and check.matchup.output.ipynb)
match_run12 = pd.read_csv('/data/cr_outs/analysis/combined/run12.csv')
match_run13 = pd.read_csv('/data/cr_outs/analysis/combined/run13.csv')
match_run14 = pd.read_csv('/data/cr_outs/analysis/combined/run14.csv')
match_run15 = pd.read_csv('/data/cr_outs/analysis/combined/run15.csv')
match_run23 = pd.read_csv('/data/cr_outs/analysis/combined/run23.csv')
match_run24 = pd.read_csv('/data/cr_outs/analysis/combined/run24.csv')
match_run25 = pd.read_csv('/data/cr_outs/analysis/combined/run25.csv')
match_run34 = pd.read_csv('/data/cr_outs/analysis/combined/run34.csv')
match_run35 = pd.read_csv('/data/cr_outs/analysis/combined/run35.csv')
match_run45 = pd.read_csv('/data/cr_outs/analysis/combined/run45.csv')

In [7]:
# Make one big super match cross table - match everything on run1
match_runs = match_run12.merge(match_run13, how = 'outer')
match_runs = match_runs.merge(match_run14, how = 'outer')
match_runs = match_runs.merge(match_run15, how = 'outer')
match_runs = match_runs.merge(match_run17, how = 'outer')
match_runs = match_runs.merge(match_run18, how = 'outer')
match_runs = match_runs.merge(match_run19, how = 'outer')
match_runs = match_runs.merge(match_run110, how = 'outer')

match_runs = match_runs.merge(match_run23, how = 'outer')
match_runs = match_runs.merge(match_run24, how = 'outer')
match_runs = match_runs.merge(match_run25, how = 'outer')
match_runs = match_runs.merge(match_run27, how = 'outer')
match_runs = match_runs.merge(match_run28, how = 'outer')
match_runs = match_runs.merge(match_run29, how = 'outer')
match_runs = match_runs.merge(match_run210, how = 'outer')


match_runs = match_runs.merge(match_run34, how = 'outer')
match_runs = match_runs.merge(match_run35, how = 'outer')
match_runs = match_runs.merge(match_run37, how = 'outer')
match_runs = match_runs.merge(match_run38, how = 'outer')
match_runs = match_runs.merge(match_run39 how = 'outer')
match_runs = match_runs.merge(match_run310 how = 'outer')

match_runs = match_runs.merge(match_run45, how = 'outer')
match_runs = match_runs.merge(match_run47, how = 'outer')
match_runs = match_runs.merge(match_run48, how = 'outer')
match_runs = match_runs.merge(match_run49, how = 'outer')
match_runs = match_runs.merge(match_run410, how = 'outer')

match_runs = match_runs.merge(match_run57, how = 'outer')
match_runs = match_runs.merge(match_run58, how = 'outer')
match_runs = match_runs.merge(match_run59, how = 'outer')
match_runs = match_runs.merge(match_run510, how = 'outer')

match_runs = match_runs.merge(match_run78, how = 'outer')
match_runs = match_runs.merge(match_run79, how = 'outer')
match_runs = match_runs.merge(match_run710, how = 'outer')

match_runs = match_runs.merge(match_run89, how = 'outer')
match_runs = match_runs.merge(match_run810, how = 'outer')

match_runs = match_runs.merge(match_run910, how = 'outer')

In [101]:
match_runs

run1  run2  run3  run4  run5
0   19.0   1.0   NaN  12.0   NaN
1   14.0   4.0   NaN   NaN   NaN
2    1.0   9.0   NaN   NaN   NaN
3    4.0  10.0   NaN   NaN   NaN
4   12.0  18.0   NaN   NaN   NaN
5    3.0   7.0   6.0   NaN   NaN
6    5.0   NaN   3.0   NaN   NaN
7    NaN  11.0   5.0   NaN   NaN
8    NaN  13.0   NaN   2.0   NaN
9    NaN  21.0   NaN  13.0   NaN
10  17.0   2.0   9.0   NaN  10.0
11   9.0   5.0   NaN   NaN   0.0
12   NaN  13.0   NaN   NaN   5.0
13   NaN  12.0   NaN   NaN  15.0
14   NaN  21.0   NaN   NaN  21.0
15  18.0   6.0  14.0   NaN  11.0
16  10.0   8.0   7.0   NaN   1.0
17  13.0  14.0  17.0  10.0  20.0
18  11.0  16.0  12.0   4.0  14.0
19   2.0   NaN   2.0   9.0   8.0
20  20.0   NaN  10.0   6.0   NaN
21  16.0   NaN  11.0   1.0  22.0
22   NaN   NaN  20.0   3.0   NaN
23   NaN   NaN   0.0   5.0   NaN
24   NaN   NaN   8.0   8.0   NaN
25   NaN   NaN  19.0  11.0   NaN
26   NaN   NaN  21.0  17.0   NaN
27   NaN   NaN   0.0   NaN   2.0
28   NaN   NaN   4.0   NaN   7.0
29   NaN   NaN  13.0   NaN   9.0
30   NaN   NaN  16.0   NaN  12.0
31   NaN   NaN  19.0   NaN  16.0
32   NaN   NaN  18.0   NaN  17.0
33   NaN   NaN  21.0   NaN  18.0
34   NaN   NaN   NaN   5.0   2.0
35   NaN   NaN   NaN   0.0   3.0
36   NaN   NaN   NaN   2.0   5.0
37   NaN   NaN   NaN  15.0   6.0
38   NaN   NaN   NaN  11.0  16.0
39   NaN   NaN   NaN  17.0  18.0
40   NaN   NaN   NaN  13.0  21.0
41   NaN   NaN   NaN  16.0  23.0

In [110]:
# Write assignment in csv file
match_runs.to_csv('/data/cr_outs/analysis/combined/match_runs.csv')

**Confirmed that everything overlaps with each other + did cross-checks with other meta data (covid.runs.tidy)**

**Added donor assignment info** based on vcf matching output txt files (from Notebooks George check.matchup.sc.output.ipynb and check.matchup.output.ipynb)

In [221]:
# Load the final donor assignments - made in excel based on vcf matching output txt + match_runs.csv file (above)
run1_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run1_final.csv')
run2_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run2_final.csv')
run3_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run3_final.csv')
run4_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run4_final.csv')
run5_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run5_final.csv')
run7_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run7_final.csv')
run8_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run8_final.csv')
run9_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run9_final.csv')
run10_final = pd.read_csv('/data/cr_outs/analysis/combined/final_assignments/run10_final.csv')

In [222]:
# Remove donor first if adding an updated version
# del adata_combat.obs['donor']

In [223]:
# Take only the individual runs (here: run1 subset) before assigning donor name to freemux_cluster - otherwise same freemux_cluster names per run
adata_combat_run1 = adata_combat[adata_combat.obs['run'].isin(['200423_run1'])]
adata_combat_run2 = adata_combat[adata_combat.obs['run'].isin(['200501_run2'])]
adata_combat_run3 = adata_combat[adata_combat.obs['run'].isin(['200520_run3'])]
adata_combat_run4 = adata_combat[adata_combat.obs['run'].isin(['200527_run4'])]
adata_combat_run5 = adata_combat[adata_combat.obs['run'].isin(['200605_run5'])]
adata_combat_run7 = adata_combat[adata_combat.obs['run'].isin(['200724_run7'])]
adata_combat_run8 = adata_combat[adata_combat.obs['run'].isin(['200806_run8'])]
adata_combat_run9 = adata_combat[adata_combat.obs['run'].isin(['200812_run9'])]
adata_combat_run10 = adata_combat[adata_combat.obs['run'].isin(['200820_run10'])]

In [224]:
# Make column onto which you merge from the same class - otherwise doesn't work (here 'int64')
adata_combat_run1.obs['freemux_cluster'] = adata_combat_run1.obs['freemux_cluster'].astype('int64')
adata_combat_run2.obs['freemux_cluster'] = adata_combat_run2.obs['freemux_cluster'].astype('int64')
adata_combat_run3.obs['freemux_cluster'] = adata_combat_run3.obs['freemux_cluster'].astype('int64')
adata_combat_run4.obs['freemux_cluster'] = adata_combat_run4.obs['freemux_cluster'].astype('int64')
adata_combat_run5.obs['freemux_cluster'] = adata_combat_run5.obs['freemux_cluster'].astype('int64')
adata_combat_run7.obs['freemux_cluster'] = adata_combat_run7.obs['freemux_cluster'].astype('int64')
adata_combat_run8.obs['freemux_cluster'] = adata_combat_run8.obs['freemux_cluster'].astype('int64')
adata_combat_run9.obs['freemux_cluster'] = adata_combat_run9.obs['freemux_cluster'].astype('int64')
adata_combat_run10.obs['freemux_cluster'] = adata_combat_run10.obs['freemux_cluster'].astype('int64')

Trying to set attribute `.obs` of view, copying.
Trying to set attribute `.obs` of view, copying.
Trying to set attribute `.obs` of view, copying.
Trying to set attribute `.obs` of view, copying.
Trying to set attribute `.obs` of view, copying.


In [225]:
# ADD DONOR ASSIGNMENT # Merge on freemux_cluster with adata_combat_run1.obs while matching on donor name (do per run seperately - otherwise not correct)
adata_combat_run1.obs = adata_combat_run1.obs.merge(run1_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run1.obs.index)
adata_combat_run2.obs = adata_combat_run2.obs.merge(run2_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run2.obs.index)
adata_combat_run3.obs = adata_combat_run3.obs.merge(run3_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run3.obs.index)
adata_combat_run4.obs = adata_combat_run4.obs.merge(run4_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run4.obs.index)
adata_combat_run5.obs = adata_combat_run5.obs.merge(run5_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run5.obs.index)
adata_combat_run7.obs = adata_combat_run7.obs.merge(run7_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run7.obs.index)
adata_combat_run8.obs = adata_combat_run8.obs.merge(run8_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run8.obs.index)
adata_combat_run9.obs = adata_combat_run9.obs.merge(run9_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run9.obs.index)
adata_combat_run10.obs = adata_combat_run10.obs.merge(run10_final, on = 'freemux_cluster', how='left').set_index(adata_combat_run10.obs.index)

**Added timepoint info**

In [226]:
# Read csv file with donor_name and timepoint and assign the correct donor to each freemux_cluster
timepoint = pd.read_csv('/data/metadata/SampleOverview_run1-6.csv', delimiter=',', dtype='str')

In [228]:
# Remove timepoint first if updating the info
# del adata_combat_run1.obs['timepoint']
# del adata_combat_run2.obs['timepoint']
# del adata_combat_run3.obs['timepoint']
# del adata_combat_run4.obs['timepoint']
# del adata_combat_run5.obs['timepoint']

# del adata_combat_run7.obs['timepoint']
# del adata_combat_run8.obs['timepoint']
# del adata_combat_run9.obs['timepoint']
# del adata_combat_run10.obs['timepoint']

In [229]:
# Delete all columns that we don't wanna merge
del timepoint['included']
del timepoint['isolation']
# Select only data from individual runs
timepoint1 = timepoint[timepoint['run'].isin(['200423_run1'])]
timepoint2 = timepoint[timepoint['run'].isin(['200501_run2'])]
timepoint3 = timepoint[timepoint['run'].isin(['200520_run3'])]
timepoint4 = timepoint[timepoint['run'].isin(['200527_run4'])]
timepoint5 = timepoint[timepoint['run'].isin(['200605_run5'])]
timepoint7 = timepoint[timepoint['run'].isin(['200724_run7'])]
timepoint8 = timepoint[timepoint['run'].isin(['200806_run8'])]
timepoint9 = timepoint[timepoint['run'].isin(['200812_run9'])]
timepoint10 = timepoint[timepoint['run'].isin(['200820_run10'])]
del timepoint1['run']
del timepoint2['run']
del timepoint3['run']
del timepoint4['run']
del timepoint5['run']
del timepoint7['run']
del timepoint8['run']
del timepoint9['run']
del timepoint10['run']

In [230]:
# ADD TIMEPOINT # Merge the timepoint info with adata_combat_run[i].obs while matching on donor name (do per run seperately - otherwise not correct)
adata_combat_run1.obs = adata_combat_run1.obs.merge(timepoint1, on = 'donor', how='left').set_index(adata_combat_run1.obs.index)
adata_combat_run2.obs = adata_combat_run2.obs.merge(timepoint2, on = 'donor', how='left').set_index(adata_combat_run2.obs.index)
adata_combat_run3.obs = adata_combat_run3.obs.merge(timepoint3, on = 'donor', how='left').set_index(adata_combat_run3.obs.index)
adata_combat_run4.obs = adata_combat_run4.obs.merge(timepoint4, on = 'donor', how='left').set_index(adata_combat_run4.obs.index)
adata_combat_run5.obs = adata_combat_run5.obs.merge(timepoint5, on = 'donor', how='left').set_index(adata_combat_run5.obs.index)
adata_combat_run7.obs = adata_combat_run7.obs.merge(timepoint7, on = 'donor', how='left').set_index(adata_combat_run7.obs.index)
adata_combat_run8.obs = adata_combat_run8.obs.merge(timepoint8 on = 'donor', how='left').set_index(adata_combat_run8.obs.index)
adata_combat_run9.obs = adata_combat_run9.obs.merge(timepoint9, on = 'donor', how='left').set_index(adata_combat_run9.obs.index)
adata_combat_run10.obs = adata_combat_run10.obs.merge(timepoint10, on = 'donor', how='left').set_index(adata_combat_run10.obs.index)

In [238]:
# Somehow this assignment doesn't work automatically - so correct this:
adata_combat_run3.obs.loc[adata_combat_run3.obs['donor'] == 'Rep_C_1044', 'timepoint'] = '0'

In [239]:
donor44 = adata_combat_run3[adata_combat_run3.obs['donor'] == 'Rep_C_1044']

In [240]:
donor44.obs[['donor', 'timepoint', 'run']]

donor timepoint          run
AAACCTGAGGTACTCT-1-0-2  Rep_C_1044         0  200520_run3
AAAGATGCACGGACAA-1-0-2  Rep_C_1044         0  200520_run3
AAAGATGCACTAAGTC-1-0-2  Rep_C_1044         0  200520_run3
AAAGATGGTTATGTGC-1-0-2  Rep_C_1044         0  200520_run3
AAAGATGTCCCACTTG-1-0-2  Rep_C_1044         0  200520_run3
...                            ...       ...          ...
TTTCCTCAGGAATTAC-1-5-2  Rep_C_1044         0  200520_run3
TTTGCGCAGGTAGCCA-1-5-2  Rep_C_1044         0  200520_run3
TTTGGTTCACGCATCG-1-5-2  Rep_C_1044         0  200520_run3
TTTGTCAAGCTGGAAC-1-5-2  Rep_C_1044         0  200520_run3
TTTGTCATCTCTAGGA-1-5-2  Rep_C_1044         0  200520_run3

[5863 rows x 3 columns]

**Added COVID status info, severity and all other clinical/phenotypic info**

In [242]:
# Combine adata_combat_run1-5 back into one object
adatas_combat = [adata_combat_run1, adata_combat_run2, adata_combat_run3, adata_combat_run4, adata_combat_run5]

In [243]:
adata_combat = adata_combat_run1.concatenate(adata_combat_run2)
adata_combat = adata_combat.concatenate(adata_combat_run3)
adata_combat = adata_combat.concatenate(adata_combat_run4)
adata_combat = adata_combat.concatenate(adata_combat_run5)

In [245]:
del adata_combat.obs['batch']

In [246]:
adata_combat.shape

(357244, 866)

In [247]:
adata = sc.read('/data/count_matrices/covid19/combined/run12345_combi_final2.h5ad')

In [248]:
# Restore original index
adata_combat.obs.index = adata.obs.index

In [140]:
# Read csv file with clinical info
covid_status = pd.read_csv('/data/metadata/COMET_patients_clinical_phenotype_info.csv', delimiter=',', dtype='str')

In [143]:
# Remove COVID_status first before updating the info
#del adata_combat.obs['COVID_status']

In [144]:
# ADD COVID status # Merge the covid_status info with adata_comba while matching on donor name
adata_combat.obs = adata_combat.obs.merge(covid_status, on = 'donor', how='left').set_index(adata_combat.obs.index)

**Added cell count info**

In [82]:
#Read csv file with cell counts
wbc_counts = pd.read_csv('/data/metadata/wbc_counts.csv', delimiter=',', dtype='str')

In [95]:
# Remove this info first if updating the Anndata object
# del adata_combat.obs['WBC_count']
#del adata_combat.obs['White_blood_cell_count']
#del adata_combat.obs['Neutrophil_count']
#del adata_combat.obs['Immature_granulocyte_count']
#del adata_combat.obs['Lymphocyte_ count']
#del adata_combat.obs['Monocyte_count']
#del adata_combat.obs['Basophil_count']
#del adata_combat.obs['Eosinophil_count']
#del adata_combat.obs['RBC_count ']

In [99]:
#Merge cell counts onto adata object
adata_combat.obs = adata_combat.obs.merge(wbc_counts[['donor', 'timepoint', 'WBC_count']],  how='left', left_on=['donor','timepoint'], right_on = ['donor','timepoint']).set_index(adata_combat.obs.index)

In [104]:
# Assign cells of timepoint='8' to timepoint = '7'
adata_combat.obs.loc[adata_combat.obs['timepoint'] == '8', 'timepoint'] = '7'

In [ ]:
# First add new category before being able to assign cells to it
adata_combat.obs['cell_type_major_low'] = adata_combat.obs['cell_type_major_low'].cat.add_categories('Megakaryocyte')

# Assign cells of cell_type_major_highres='Megakaryocyte' to cell_type_major_low = 'Megakaryocyte'
adata_combat.obs.loc[adata_combat.obs['cell_type_major_highres'] == 'Megakaryocyte', 'cell_type_major_low'] = 'Megakaryocyte'

In [271]:
# Healthy controls should be re-assigned as COVID_status = 'None'
adata_combat.obs['COVID_status'] = adata_combat.obs['COVID_status'].cat.add_categories('None')

adata_combat.obs.loc[adata_combat.obs['donor'] == 'ICC_C_0001', 'COVID_status'] = 'None'
adata_combat.obs.loc[adata_combat.obs['donor'] == 'ICC_C_0002', 'COVID_status'] = 'None'
adata_combat.obs.loc[adata_combat.obs['donor'] == 'ICC_C_0003', 'COVID_status'] = 'None'
adata_combat.obs.loc[adata_combat.obs['donor'] == 'ICC_C_0004', 'COVID_status'] = 'None'
adata_combat.obs.loc[adata_combat.obs['donor'] == 'ICC_C_0005', 'COVID_status'] = 'None'

In [15]:
# When updating newest version use:
adata_combat.write('/data/count_matrices/covid19/combined/run12345_combi_final2.h5ad')

... storing 'donor' as categorical
... storing 'severity' as categorical
